In [1]:
import os, re
import matplotlib.pyplot as plt
import SimpleITK as sitk


FIRST WE CREATE THE CONTROL GROUP IW-TSE SEGMENTATION

In [2]:
dess_nii_control_folder = '/media/anastasis/My Harddisk2/ThesisImages/OAI_DESS_control/'
iw_nii_control_folder = '/media/anastasis/My Harddisk2/ThesisImages/OAI_IW-TSE_control/'

dess_nii_control_path = sorted(os.path.join(dess_nii_control_folder,fname) for fname in os.listdir(dess_nii_control_folder))
iw_nii_control_path = sorted(os.path.join(iw_nii_control_folder,fname) for fname in os.listdir(iw_nii_control_folder))

In [3]:
dess_nii_control_path[0], len(dess_nii_control_path), iw_nii_control_path[0], len(iw_nii_control_path)

('/media/anastasis/My Harddisk2/ThesisImages/OAI_DESS_control/9001400_DESS_R.nii.gz',
 433,
 '/media/anastasis/My Harddisk2/ThesisImages/OAI_IW-TSE_control/9001400_IW-TSE_R.nii.gz',
 433)

In [4]:
dess_seg_control_folder = '/media/anastasis/My Harddisk2/ThesisImages/OAI_DESS_control_seg_nii'
dess_seg_control_path = sorted(os.path.join(dess_seg_control_folder,fname) for fname in os.listdir(dess_seg_control_folder))

In [5]:
dess_seg_control_path[350], len(dess_seg_control_path)

('/media/anastasis/My Harddisk2/ThesisImages/OAI_DESS_control_seg_nii/9786191_DESS_L.nii.gz',
 433)

In [11]:
for i in range(400,len(dess_nii_control_path)):
    iw_num = iw_nii_control_path[0].split('/')[-1].split('.')
    dess_num = dess_nii_control_path[i].split('/')[-1].split('.')

    fixed_iw = sitk.ReadImage(iw_nii_control_path[i],sitk.sitkFloat32)
    moving_dess = sitk.ReadImage(dess_nii_control_path[i],sitk.sitkFloat32)
    
    parameterMap = sitk.GetDefaultParameterMap('affine')
    # parameterMap['Transform'] = ['BSplineTransform']

    # parameterMap['FixedInternalImagePixelType'] = ['float']
    # parameterMap['FixedImageDimension'] = ['3']
    # parameterMap['MovingInternalImagePixelType'] = ['float']
    # parameterMap['MovingImageDimension'] = ['3']

    # parameterMap['Registration'] = ['MultiResolutionRegistration']
    # parameterMap['FixedImagePyramid'] = ['FixedSmoothingImagePyramid']
    # parameterMap['MovingImagePyramid'] = ['MovingSmoothingImagePyramid']
    # parameterMap['Interpolator'] = ['BSplineInterpolator']
    # parameterMap['Metric'] = ['AdvancedMattesMutualInformation']
    # parameterMap['ResampleInterpolator'] = ['FinalBSplineInterpolator']
    # parameterMap['Resampler'] = ['DefaultResampler']
    # parameterMap['Transform'] = ['AffineTransform']

    # parameterMap['ErodeMask'] = ['false']

    # parameterMap['NumberOfResolutions'] = ['4']

    # parameterMap['HowToCombineTransforms'] = ['Compose']
    # parameterMap['AutomaticTransformInitialization'] = ['true']
    # parameterMap['AutomaticScalesEstimation'] = ['true']

    # parameterMap['WriteTransformParametersEachIteration'] = ['false']
    # parameterMap['WriteResultImage'] = ['false']
    # parameterMap['CompressResultImage'] = ['false']
    # parameterMap['WriteResultImageAfterEachResolution'] = ['false']
    # parameterMap['ShowExactMetricValue'] = ['false']
    # parameterMap['ResultImagePixelType'] = ['float']
    # parameterMap['ResultImageFormal'] = ['nii']

    # parameterMap['MaximumNumberOfIterations'] = ['2500']

    # # //Number of grey level bins in each resolution level:
    # parameterMap['NumberOfHistogramBins'] =['32']  
    # parameterMap['FixedLimitRangeRatio'] =['0.0'] 
    # parameterMap['MovingLimitRangeRatio'] =['0.0'] 
    # parameterMap['FixedKernelBSplineOrder'] =['3'] 
    # parameterMap['MovingKernelBSplineOrder'] =['3'] 

    # # //Number of spatial samples used to compute the mutual information in each resolution level:
    # parameterMap['ImageSampler'] = ["RandomCoordinate"]
    # parameterMap['FixedImageBSplineInterpolationOrder']=['1']
    # parameterMap['UseRandomSampleRegion']= ["true"]
    # parameterMap['NumberOfSpatialSamples']= [ '3500' ]
    # parameterMap['NewSamplesEveryIteration']= ["true"]
    # parameterMap['CheckNumberOfSamples']= ["true"]
    # parameterMap['MaximumNumberOfSamplingAttempts']= ['10']

    # # //Order of B-Spline interpolation used in each resolution level:
    # parameterMap['BSplineInterpolationOrder'] = ['1']
    # # //Order of B-Spline interpolation used for applying the final deformation:
    # parameterMap['FinalBSplineInterpolationOrder'] = ['3'] 
    # # //Default pixel value for pixels that come from outside the picture:
    # parameterMap['DefaultPixelValue'] = ['0']
    # # //SP: Param_alpha in each resolution level. a_k = a/(A+k+1)^alpha
    # parameterMap['SP_alpha']= ['0.6'] 

    elastixImageFilter = sitk.ElastixImageFilter()
    elastixImageFilter.SetFixedImage(fixed_iw)
    elastixImageFilter.SetMovingImage(moving_dess)
    elastixImageFilter.SetParameterMap(parameterMap)
    elastixImageFilter.Execute()

    iw_fixed_dess_moving = elastixImageFilter.GetResultImage()
    savepath1 = '/media/anastasis/My Harddisk2/ThesisImages/OAI_IW_fixed_DESS_moving_control/'
    sitk.WriteImage(iw_fixed_dess_moving,os.path.join(savepath1,dess_num[0]+'_iw_f_dess_m_reg.nii.gz'))

    moving_dess_mask = sitk.ReadImage(dess_seg_control_path[i])
    moving_dess_mask = 4*(moving_dess_mask/255)
    transformParameterMap = elastixImageFilter.GetTransformParameterMap()
    transformix = sitk.TransformixImageFilter()
    transformix.SetTransformParameterMap(transformParameterMap)
    transformix.SetMovingImage(moving_dess_mask)
    transformix.Execute()

    RoundImage = sitk.RoundImageFilter()
    rounded_mask = RoundImage.Execute(transformix.GetResultImage())
    savepath2 = '/media/anastasis/My Harddisk2/ThesisImages/OAI_IW-TSE_control_seg/'
    sitk.WriteImage(rounded_mask,os.path.join(savepath2,dess_num[0]+'_seg.nii.gz'))

    # if i ==1:
    #     break

ELASTIX version: 5.000
Command line options from ElastixBase:
-fMask    unspecified, so no fixed mask used
-mMask    unspecified, so no moving mask used
-out      ./
-threads  unspecified, so all available threads are used
  The default value "true" is used instead.

  From elastix 4.8 it defaults to true!
This may change the behavior of your registrations considerably.

Command line options from TransformBase:
-t0       unspecified, so no initial transform used

Reading images...
Reading images took 0 ms.

  A default pyramid schedule is used.
  A default pyramid schedule is used.
  The default value "false" is used instead.
  The default value "GeometricalCenter" is used instead.
Transform parameters are initialized as: [1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0]
InitializeTransform took 0.00s
Scales are estimated automatically.
Scales for transform parameters are: [1632.672303311917, 1679.2825222548868, 1633.3606554748458, 1632.672303311917, 1679.2825222548868, 1633.3606554748458, 1632.672

NOW WE CREATE THE PROGRESS SEGMENTATION

In [12]:
dess_nii_progress_folder = '/media/anastasis/My Harddisk2/ThesisImages/OAI_DESS_progress/'
iw_nii_progress_folder = '/media/anastasis/My Harddisk2/ThesisImages/OAI_IW-TSE_progress/'

dess_nii_progress_path = sorted(os.path.join(dess_nii_progress_folder,fname) for fname in os.listdir(dess_nii_progress_folder))
iw_nii_progress_path = sorted(os.path.join(iw_nii_progress_folder,fname) for fname in os.listdir(iw_nii_progress_folder))

In [13]:
dess_nii_progress_path[0], len(dess_nii_progress_path), iw_nii_progress_path[0], len(iw_nii_progress_path)

('/media/anastasis/My Harddisk2/ThesisImages/OAI_DESS_progress/9002316_DESS_L.nii.gz',
 159,
 '/media/anastasis/My Harddisk2/ThesisImages/OAI_IW-TSE_progress/9002316_IW-TSE_L.nii.gz',
 159)

In [14]:
dess_seg_progress_folder = '/media/anastasis/My Harddisk2/ThesisImages/OAI_DESS_progress_seg_nii'
dess_seg_progress_path = sorted(os.path.join(dess_seg_progress_folder,fname) for fname in os.listdir(dess_seg_progress_folder))

In [15]:
bla = dess_seg_progress_path[0].split('/')[-1].split('.')[0]
dess_seg_progress_path[0], len(dess_seg_progress_path), bla

('/media/anastasis/My Harddisk2/ThesisImages/OAI_DESS_progress_seg_nii/9002316_DESS_L.nii.gz',
 159,
 '9002316_DESS_L')

In [17]:

for i in range(100,len(dess_nii_progress_path)):
    iw_num = iw_nii_progress_path[0].split('/')[-1].split('.')
    dess_num = dess_nii_progress_path[i].split('/')[-1].split('.')

    fixed_iw = sitk.ReadImage(iw_nii_progress_path[i],sitk.sitkFloat32)
    moving_dess = sitk.ReadImage(dess_nii_progress_path[i],sitk.sitkFloat32)
    
    parameterMap = sitk.GetDefaultParameterMap('affine')
    # parameterMap['Transform'] = ['BSplineTransform']

    # parameterMap['FixedInternalImagePixelType'] = ['float']
    # parameterMap['FixedImageDimension'] = ['3']
    # parameterMap['MovingInternalImagePixelType'] = ['float']
    # parameterMap['MovingImageDimension'] = ['3']

    # parameterMap['Registration'] = ['MultiResolutionRegistration']
    # parameterMap['FixedImagePyramid'] = ['FixedSmoothingImagePyramid']
    # parameterMap['MovingImagePyramid'] = ['MovingSmoothingImagePyramid']
    # parameterMap['Interpolator'] = ['BSplineInterpolator']
    # parameterMap['Metric'] = ['AdvancedMattesMutualInformation']
    # parameterMap['ResampleInterpolator'] = ['FinalBSplineInterpolator']
    # parameterMap['Resampler'] = ['DefaultResampler']
    # parameterMap['Transform'] = ['AffineTransform']

    # parameterMap['ErodeMask'] = ['false']

    # parameterMap['NumberOfResolutions'] = ['4']

    # parameterMap['HowToCombineTransforms'] = ['Compose']
    # parameterMap['AutomaticTransformInitialization'] = ['true']
    # parameterMap['AutomaticScalesEstimation'] = ['true']

    # parameterMap['WriteTransformParametersEachIteration'] = ['false']
    # parameterMap['WriteResultImage'] = ['false']
    # parameterMap['CompressResultImage'] = ['false']
    # parameterMap['WriteResultImageAfterEachResolution'] = ['false']
    # parameterMap['ShowExactMetricValue'] = ['false']
    # parameterMap['ResultImagePixelType'] = ['float']
    # parameterMap['ResultImageFormal'] = ['nii']

    # parameterMap['MaximumNumberOfIterations'] = ['2500']

    # # //Number of grey level bins in each resolution level:
    # parameterMap['NumberOfHistogramBins'] =['32']  
    # parameterMap['FixedLimitRangeRatio'] =['0.0'] 
    # parameterMap['MovingLimitRangeRatio'] =['0.0'] 
    # parameterMap['FixedKernelBSplineOrder'] =['3'] 
    # parameterMap['MovingKernelBSplineOrder'] =['3'] 

    # # //Number of spatial samples used to compute the mutual information in each resolution level:
    # parameterMap['ImageSampler'] = ["RandomCoordinate"]
    # parameterMap['FixedImageBSplineInterpolationOrder']=['1']
    # parameterMap['UseRandomSampleRegion']= ["true"]
    # parameterMap['NumberOfSpatialSamples']= [ '3500' ]
    # parameterMap['NewSamplesEveryIteration']= ["true"]
    # parameterMap['CheckNumberOfSamples']= ["true"]
    # parameterMap['MaximumNumberOfSamplingAttempts']= ['10']

    # # //Order of B-Spline interpolation used in each resolution level:
    # parameterMap['BSplineInterpolationOrder'] = ['1']
    # # //Order of B-Spline interpolation used for applying the final deformation:
    # parameterMap['FinalBSplineInterpolationOrder'] = ['3'] 
    # # //Default pixel value for pixels that come from outside the picture:
    # parameterMap['DefaultPixelValue'] = ['0']
    # # //SP: Param_alpha in each resolution level. a_k = a/(A+k+1)^alpha
    # parameterMap['SP_alpha']= ['0.6'] 

    elastixImageFilter = sitk.ElastixImageFilter()
    elastixImageFilter.SetFixedImage(fixed_iw)
    elastixImageFilter.SetMovingImage(moving_dess)
    elastixImageFilter.SetParameterMap(parameterMap)
    elastixImageFilter.Execute()

    iw_fixed_dess_moving = elastixImageFilter.GetResultImage()
    savepath1 = '/media/anastasis/My Harddisk2/ThesisImages/OAI_IW_fixed_DESS_moving_progress/'
    sitk.WriteImage(iw_fixed_dess_moving,os.path.join(savepath1,dess_num[0]+'_iw_f_dess_m_reg.nii.gz'))

    moving_dess_mask = sitk.ReadImage(dess_seg_progress_path[i])
    moving_dess_mask = 4*(moving_dess_mask/255)
    transformParameterMap = elastixImageFilter.GetTransformParameterMap()
    transformix = sitk.TransformixImageFilter()
    transformix.SetTransformParameterMap(transformParameterMap)
    transformix.SetMovingImage(moving_dess_mask)

    transformix.Execute()

    RoundImage = sitk.RoundImageFilter()
    rounded_mask = RoundImage.Execute(transformix.GetResultImage())
    savepath2 = '/media/anastasis/My Harddisk2/ThesisImages/OAI_IW-TSE_progress_seg/'
     
    sitk.WriteImage(rounded_mask,os.path.join(savepath2,dess_num[0]+'_seg.nii.gz'))

    # if i ==1:
    #     break

ELASTIX version: 5.000
Command line options from ElastixBase:
-fMask    unspecified, so no fixed mask used
-mMask    unspecified, so no moving mask used
-out      ./
-threads  unspecified, so all available threads are used
  The default value "true" is used instead.

  From elastix 4.8 it defaults to true!
This may change the behavior of your registrations considerably.

Command line options from TransformBase:
-t0       unspecified, so no initial transform used

Reading images...
Reading images took 0 ms.

  A default pyramid schedule is used.
  A default pyramid schedule is used.
  The default value "false" is used instead.
  The default value "GeometricalCenter" is used instead.
Transform parameters are initialized as: [1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0]
InitializeTransform took 0.00s
Scales are estimated automatically.
Scales for transform parameters are: [1632.672019366079, 1679.2828062126082, 1633.3606554629384, 1632.672019366079, 1679.2828062126082, 1633.3606554629384, 1632.672